Injection began on November 17, 2011 into the Mount Simon Sandstone at a depth of approximately 7,000 feet (2,100 meters) and were successfully carried out by November 26, 2014. During this three-year period, a substantial amount of data was collected.

To monitor temperature changes, a distributed temperature sensor (DTS) fiber optic cable was installed in the tubing, extending to a depth of 6,326 feet and recording temperature every 1.624 feet every 5 seconds. Utilizing the first two years of injection data (rate, pressure, temperature) from the injector and the corresponding fiber optic DTS temperature profile from the observation well, we aim to apply machine learning methods to predict the injection rate delta. The predicted injection rate deltas determined from the monitoring well, fiber optic data and other injection well attributes can be compared to the actual injection rate as an additional way to verify reservoir integrity.

In [206]:
import pandas as pd
import numpy as np
import plotly.express as px
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split

In [207]:
df = pd.read_csv('data/illinois_basing_train.csv')
df["SampleTimeUTC"] = pd.to_datetime(df["SampleTimeUTC"])
df.sort_values(by="SampleTimeUTC", inplace=True)
df.sample(10)

SampleTimeUTC  Avg_PLT_CO2InjRate_TPH  Avg_PLT_CO2VentRate_TPH  \
11593 2011-01-28 10:00:00               45.065278                 0.000000   
20889 2012-02-20 06:00:00               44.657985                 0.075000   
5034  2010-04-29 17:00:00               41.174653                 3.850000   
4894  2010-04-23 21:00:00               40.833328                 4.000000   
7966  2010-08-29 22:00:00               43.244445                 0.041667   
26501 2012-11-10 23:00:00                0.000000                 0.000000   
3991  2010-03-16 14:00:00                0.000000                 0.000000   
11162 2011-10-01 07:00:00               46.298959                 0.000000   
7815  2010-08-23 15:00:00               43.050000                 0.016667   
23419 2012-04-06 16:00:00               43.220140                 0.033333   

       Avg_CCS1_WHCO2InjPs_psi  Avg_CCS1_WHCO2InjTp_F  Avg_CCS1_ANPs_psi  \
11593              1348.984236              96.056191         627.202395   
20889              1345.573706              96.152138         511.147919   
5034               1315.019103              96.482457         587.485889   
4894                  0.000000               0.000000           0.000000   
7966               1355.179289              97.871134         554.764942   
26501               893.107422              59.424302         519.842310   
3991               1158.383973              88.232094         568.045313   
11162              1345.777381              96.104897         611.373452   
7815               1361.002196              98.744544         690.780819   
23419              1361.414323              96.786047         629.613548   

       Avg_CCS1_DH6325Ps_psi  Avg_CCS1_DH6325Tp_F  Avg_VW1_WBTbgPs_psi  \
11593            3294.035160           131.428200             0.000000   
20889            3420.432558           129.673886             0.000000   
5034             3270.608746           129.994406          2275.287018   
4894             3266.995024           129.956204          2276.510575   
7966             3317.405518           131.194257          2292.641374   
26501            3027.248617           121.302250          2322.514470   
3991             3133.441628           126.101892             0.000000   
11162            3309.676701           131.122727             0.000000   
7815             3299.901540           131.199195          2292.258840   
23419            3408.688780           130.192035          2411.262307   

       Avg_VW1_WBTbgTp_F  ...  Avg_VW1_Z04D6837Tp_F  Avg_VW1_Z03D6945Ps_psi  \
11593           0.000000  ...              0.000000                0.000000   
20889           0.000000  ...              0.000000                0.000000   
5034          106.806940  ...            119.514327             3329.124416   
4894          106.730502  ...            119.573202             3329.209332   
7966          108.864550  ...            118.850427             3327.724589   
26501         104.907875  ...            122.683710                0.000000   
3991            0.000000  ...              0.000000                0.000000   
11162           0.000000  ...              0.000000                0.000000   
7815          108.479109  ...            119.127850             3327.248633   
23419         105.869951  ...            122.348949                     NaN   

       Avg_VW1_Z03D6945Tp_F  Avg_VW1_Z02D6982Ps_psi  Avg_VW1_Z02D6982Tp_F  \
11593              0.000000                0.000000              0.000000   
20889              0.000000                0.000000              0.000000   
5034             120.465716             3307.901351            121.617341   
4894             120.373359             3309.355731            121.646140   
7966             122.025743             3350.115790            122.974902   
26501              0.000000             3258.498326            122.891391   
3991               0.000000                0.000000              0.000000   
11162          

In [208]:
df.rename(columns={'inj_diff\xa0': 'inj_diff'}, inplace=True)
fig = px.line(df, x="SampleTimeUTC", y="inj_diff", title="CO2 Inj Delta vs. Prior Hour", width=800)
fig.show()

It looks like there's a data bust on november 4, 2009. Let's remove that.

In [209]:
df = df[df["inj_diff"].abs() < 1000]
fig = px.line(df, x="SampleTimeUTC", y="inj_diff", title="CO2 Inj Delta vs. Prior Hour", width=800)
fig.show()

In [210]:
fig = px.line(df, x="SampleTimeUTC", y="Avg_PLT_CO2InjRate_TPH", title="CO2 Injection By Hour", width=800)
fig.show()

In [211]:
# the data from before November 2009 looks pretty bad, so let's drop it
df = df[df["SampleTimeUTC"] > "2009-11-12"]
fig = px.line(df, x="SampleTimeUTC", y="Avg_PLT_CO2InjRate_TPH", title="CO2 Injection By Hour", width=800)
fig.show()

So it looks like the injection rate is mostly constant, but there are some significant spikes where the injection rate drops near to zero and later recovers. Predicting those spikes from the offset details going to be crucial to the success of this model, especially since we're graded on RSME.

## Modeling Approach

To train our model, we will split our dataset by time to avoid data leakage into the test set. We will use the first 80% of the data to train our model and the last 20% to test it.

In [212]:
train_df = df[df["SampleTimeUTC"] < "2012-04-20"]
test_df = df[df["SampleTimeUTC"] >= "2012-04-20"]
print(f"Train set contains {train_df.shape[0]} rows.")
print(f"Test set contains {test_df.shape[0]} rows.")
print(train_df.shape[0] / (train_df.shape[0] + test_df.shape[0]))

Train set contains 21002 rows.
Test set contains 5171 rows.
0.802429985099148


Let's zoom in on a single event to see what happened across all the trends when the injection rate dropped to zero.

In [213]:
# filter to august 19, 2010
one_event_df = train_df[(train_df["SampleTimeUTC"] >= "2010-08-19") & (train_df["SampleTimeUTC"] < "2010-08-20")]
fig = px.line(one_event_df, x="SampleTimeUTC", y="inj_diff", title="CO2 Injection By Hour", width=800)
fig.show()

In [214]:
one_event_long_df = one_event_df.melt(id_vars=["SampleTimeUTC"])
fig = px.line(one_event_long_df, x="SampleTimeUTC", y="value", color="variable", width=800)
fig.show()

By playing around with the different features on the plot, I can see around half of them are obviously correlated with the injection rate. However let's fit a model on all features at first. We'll also create some lagged/leading/delta features to capture the time series nature of the data.

In [215]:
# create lagged feature for all columns in train_df
def make_features(df_old):
    lagged_df = df_old.copy()
    lead_df = df_old.copy()
    lagged_df["SampleTimeUTC"] = lagged_df["SampleTimeUTC"] + pd.DateOffset(hours=1)
    lead_df["SampleTimeUTC"] = lead_df["SampleTimeUTC"] - pd.DateOffset(hours=1)
    # rename all columns to have _lag1hr on the end
    lagged_df = lagged_df.add_suffix('_lag1hr')
    lead_df = lead_df.add_suffix('_lead1hr')  # rename all columns to have _lead1hr on the end
    # join into the main dataframe
    new_df = df_old.merge(lagged_df, how="left", left_on="SampleTimeUTC", right_on="SampleTimeUTC_lag1hr")
    new_df = new_df.merge(lead_df, how="left", left_on="SampleTimeUTC", right_on="SampleTimeUTC_lead1hr")
    new_df.drop(columns=["SampleTimeUTC", "SampleTimeUTC_lag1hr", "SampleTimeUTC_lead1hr"], inplace=True)
    return new_df

In [230]:
X_train = train_df.drop(columns=["inj_diff", "Avg_PLT_CO2InjRate_TPH"]).copy()
X_test = test_df.drop(columns=["inj_diff", "Avg_PLT_CO2InjRate_TPH"]).copy()
y_train = train_df["inj_diff"]
y_test = test_df["inj_diff"]
X_train.head()

SampleTimeUTC  Avg_PLT_CO2VentRate_TPH  Avg_CCS1_WHCO2InjPs_psi  \
1705 2009-11-12 01:00:00                      0.0              1320.037872   
1706 2009-11-12 02:00:00                      0.0              1315.738935   
1707 2009-11-12 03:00:00                      0.0              1316.543107   
1708 2009-11-12 04:00:00                      0.0              1309.126712   
1709 2009-11-12 05:00:00                      0.0              1308.357270   

      Avg_CCS1_WHCO2InjTp_F  Avg_CCS1_ANPs_psi  Avg_CCS1_DH6325Ps_psi  \
1705              94.244911         605.374011            3280.041500   
1706              93.765542         575.733179            3280.998289   
1707              94.423257         571.788085            3277.288481   
1708              92.783730         579.754660            3279.223661   
1709              93.413613         597.834790            3280.458738   

      Avg_CCS1_DH6325Tp_F  Avg_VW1_WBTbgPs_psi  Avg_VW1_WBTbgTp_F  \
1705           127.725802          2231.222260         104.169261   
1706           127.656590          2231.231710         104.170326   
1707           127.488470          2231.203951         104.170326   
1708           127.407359          2231.223267         104.180976   
1709           127.229922          2231.201213         104.159676   

      Avg_VW1_ANPs_psi  ...  Avg_VW1_Z04D6837Ps_psi  Avg_VW1_Z04D6837Tp_F  \
1705          1.707459  ...             3119.782100            119.875753   
1706          1.669922  ...             3119.783195            119.871238   
1707          1.647949  ...             3119.792505            119.878333   
1708          1.617737  ...             3119.766154            119.868658   
1709          1.604919  ...             3119.806128            119.854468   

      Avg_VW1_Z03D6945Ps_psi  Avg_VW1_Z03D6945Tp_F  Avg_VW1_Z02D6982Ps_psi  \
1705             3294.069446            121.131717             3309.825759   
1706             3294.379911            121.131012             3310.149762   
1707             3294.692397            121.151007             3310.443323   
1708             3295.027787            121.145772             3310.716551   
1709             3295.332461            121.140867             3310.981089   

      Avg_VW1_Z02D6982Tp_F  Avg_VW1_Z01D7061Ps_psi  Avg_VW1_Z01D7061Tp_F  \
1705            121.654450             3253.627641            122.714607   
1706            121.621826             3253.749359            122.706912   
1707            121.614671             3253.867293            122.713032   
1708            121.604337             3253.983331            122.715312   
1709            121.630571             3254.078131            122.709972   

      Avg_VW1_Z0910D5482Ps_psi  Avg_VW1_Z0910D5482Tp_F  
1705               2376.198651              112.505738  
1706               2376.158582              112.505738  
1707               2376.132931              112.505738  
1708               2376.098140              112.515098  
1709               2376.073480              112.515818  

[5 rows x 34 columns]

In [231]:
X_train = make_features(X_train)#.dropna(inplace=True)
X_test = make_features(X_test)#.dropna(inplace=True)
X_train.head()

Avg_PLT_CO2VentRate_TPH  Avg_CCS1_WHCO2InjPs_psi  Avg_CCS1_WHCO2InjTp_F  \
0                      0.0              1320.037872              94.244911   
1                      0.0              1315.738935              93.765542   
2                      0.0              1316.543107              94.423257   
3                      0.0              1309.126712              92.783730   
4                      0.0              1308.357270              93.413613   

   Avg_CCS1_ANPs_psi  Avg_CCS1_DH6325Ps_psi  Avg_CCS1_DH6325Tp_F  \
0         605.374011            3280.041500           127.725802   
1         575.733179            3280.998289           127.656590   
2         571.788085            3277.288481           127.488470   
3         579.754660            3279.223661           127.407359   
4         597.834790            3280.458738           127.229922   

   Avg_VW1_WBTbgPs_psi  Avg_VW1_WBTbgTp_F  Avg_VW1_ANPs_psi  \
0          2231.222260         104.169261          1.707459   
1          2231.231710         104.170326          1.669922   
2          2231.203951         104.170326          1.647949   
3          2231.223267         104.180976          1.617737   
4          2231.201213         104.159676          1.604919   

   Avg_VW1_Z11D4917Ps_psi  ...  Avg_VW1_Z04D6837Ps_psi_lead1hr  \
0             2073.597243  ...                     3119.783195   
1             2073.560203  ...                     3119.792505   
2             2073.519808  ...                     3119.766154   
3             2073.486037  ...                     3119.806128   
4             2073.549609  ...                     3119.822957   

   Avg_VW1_Z04D6837Tp_F_lead1hr  Avg_VW1_Z03D6945Ps_psi_lead1hr  \
0                    119.871238                     3294.379911   
1                    119.878333                     3294.692397   
2                    119.868658                     3295.027787   
3                    119.854468                     3295.332461   
4                    119.853178                     3295.604480   

   Avg_VW1_Z03D6945Tp_F_lead1hr  Avg_VW1_Z02D6982Ps_psi_lead1hr  \
0                    121.131012                     3310.149762   
1                    121.151007                     3310.443323   
2                    121.145772                     3310.716551   
3                    121.140867                     3310.981089   
4                    121.126931                     3311.287821   

   Avg_VW1_Z02D6982Tp_F_lead1hr  Avg_VW1_Z01D7061Ps_psi_lead1hr  \
0                    121.621826                     3253.749359   
1                    121.614671                     3253.867293   
2                    121.604337                     3253.983331   
3                    121.630571                     3254.078131   
4                    121.640111                     3254.209623   

   Avg_VW1_Z01D7061Tp_F_lead1hr  Avg_VW1_Z0910D5482Ps_psi_lead1hr  \
0                    122.706912                       2376.158582   
1                    122.713032                       2376.132931   
2                    122.715312                       2376.098140   
3                    122.709972                       2376.073480   
4                    122.711502                       2376.093831   

   Avg_VW1_Z0910D5482Tp_F_lead1hr  
0                      112.505738  
1                      112.505738  
2                      112.515098  
3                      112.515818  
4                      112.521578  

[5 rows x 99 columns]

In [233]:
counts = pd.DataFrame(X_train.isna().sum()).reset_index()
counts.sort_values(by=0, ascending=False, inplace=True)
fig = px.bar(counts.head(100), x=0, y="index", title="Missing", width=800)
fig.show()

In [234]:
# rather than dropping records with NANs, let's fill them with the mean
X_train.fillna(X_train.mean(), inplace=True)
X_test.fillna(X_test.mean(), inplace=True)

In [235]:
# train a simple linear regression model
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error


lr = LinearRegression()
lr.fit(X_train, y_train)
y_pred = lr.predict(X_test)
print(f"RMSE: {np.sqrt(mean_squared_error(y_test, y_pred))}")

RMSE: 3.1083323717029363


In [237]:
# plot predicted vs actuals
fig = px.scatter(x=y_test, y=y_pred, title="Predicted vs. Actuals", width=800)
fig.show()

It looks like we overfit. That's unsurprising since we have so many features. Let's try to reduce the number of features by using a random forest to select the most important features.

In [238]:
# fit random forest model
from sklearn.ensemble import RandomForestRegressor
rf = RandomForestRegressor()
rf.fit(X_train, y_train)
y_pred = rf.predict(X_test)
print(f"RMSE: {np.sqrt(mean_squared_error(y_test, y_pred))}")

RMSE: 2.092373972441748


In [239]:
# show variable importance
importances = pd.DataFrame({"feature": X_train.columns, "importance": rf.feature_importances_})
importances.sort_values(by="importance", ascending=True, inplace=True)
fig = px.bar(importances.head(30), x="importance", y="feature", title="Variable Importance", width=800)
fig.show()

In [240]:
# now train an xgboost model
import xgboost as xgb
xgb_model = xgb.XGBRegressor()
xgb_model.fit(X_train, y_train)
y_pred = xgb_model.predict(X_test)
print(f"RMSE: {np.sqrt(mean_squared_error(y_test, y_pred))}")

RMSE: 1.985588927122332


In [245]:
# show rmse on training set
y_pred = xgb_model.predict(X_train)
print(f"RMSE: {np.sqrt(mean_squared_error(y_train, y_pred))}")

RMSE: 0.5238710923426845


So we're overfit a bit.

In [241]:
# show variable importance
importances = pd.DataFrame({"feature": X_train.columns, "importance": xgb_model.feature_importances_})
importances.sort_values(by="importance", ascending=True, inplace=True)
fig = px.bar(importances.head(30), x="importance", y="feature", title="Variable Importance", width=800)
fig.show()

## Final Model

XGboost performed the best, so we use it to train a final model on both the test and train data.

In [246]:
X_all = df.drop(columns=["inj_diff", "Avg_PLT_CO2InjRate_TPH"]).copy()
y_all = df["inj_diff"]
X_all = make_features(X_all)
X_all.fillna(X_all.mean(), inplace=True)

In [248]:
# now train xgboost on all data
xgb_model = xgb.XGBRegressor()
xgb_model.fit(X_all, y_all)
y_pred = xgb_model.predict(X_all)
print(f"RMSE: {np.sqrt(mean_squared_error(y_all, y_pred))}")  # compare this to the RMSE on the training set from before

RMSE: 0.5243150560167883


Weirdly, we didn't get any better. 